# Relating number of COVID-19 deaths and cases
> Death rates, Infection-spread rates &  Infections Per million Popolation

- comments: true
- author: Guneet Singh
- categories: [rate, compare, growth]
- hide: false
- image: images/deth_rate_comparision.png
- permalink: /covid-compare-death-rate/

In [ ]:
#hide
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import altair as alt
%config InlineBackend.figure_format = 'retina'
import load_covid_data 
import utils
chart_width = 550
chart_height= 400
atLeast= 1000
moreThan= 5000000
data = utils.getComulativeData('confirmed')
ddata = utils.getComulativeData('deaths')


In [ ]:
#hide
def death_rate(totalDeath,totalCases):
    if totalCases!=0 :
        return (each['total_deaths'][i]/each['total_confirmed'][i])*100 
    else: return 0

country_data=[]
for i in data.location.unique():
    filter_country = data["location"]== i
    temp=data[filter_country]
    temp['total_deaths']=ddata[filter_country]['total_deaths']
    temp=temp.reset_index()
    temp=temp.drop('index',axis=1)
    country_data.append(temp)

every_country_data=pd.DataFrame(columns={'location', 'date', 'total_confirmed','total_deaths','percent_change','death_percent_change','death_rate'})
for each in country_data :
    each['percent_change']=None
    each['death_percent_change']=None
    each['death_rate']=None
    for i in range(each.total_confirmed.size):
         each['percent_change'][i]=utils.toPercent(i,each['total_confirmed'][i],each['total_confirmed'])
         each['death_percent_change'][i]=utils.toPercent(i,each['total_deaths'][i],each['total_deaths'])
         each['death_rate'][i]=death_rate(each['total_confirmed'][i],each['total_deaths'][i])
    # display(each)
    every_country_data=every_country_data.append(each)

temp_rank_data=pd.DataFrame(columns=['country','total'])#,data={'country':data.location.unique(),'total':None})
for each in country_data:
        # if each.death_rate.tail(1).to_list()[0]>0:
    if each.total_confirmed.tail(1).to_list()[0]>moreThan:
        temp_rank_data=temp_rank_data.append([{'country':each.location[0],'total':each.death_rate.tail(1).to_list()[0]}])
temp_rank_data=temp_rank_data.sort_values(by='total',ascending=False)
# temp_rank_data


In [ ]:
#hide
countries=temp_rank_data.country[0:20]
cases_countries=temp_rank_data.country[temp_rank_data["total"]>1]
# display(cases_countries)
country_data=[]
for i in countries:
    filter_country = data["location"]== i
    temp=data[filter_country]
    temp['total_deaths']=ddata[filter_country]['total_deaths']
    temp=temp.reset_index()
    temp=temp.drop('index',axis=1)
    country_data.append(temp)

every_country_data=pd.DataFrame(columns={'location', 'date', 'total_confirmed','total_deaths','percent_change','death_percent_change','death_rate'})
for each in country_data :
    each['percent_change']=None
    each['death_percent_change']=None
    each['death_rate']=None
    for i in range(each.total_confirmed.size):
         each['percent_change'][i]=utils.toPercent(i,each['total_confirmed'][i],each['total_confirmed'])
         each['death_percent_change'][i]=utils.toPercent(i,each['total_deaths'][i],each['total_deaths'])
         each['death_rate'][i]=death_rate(each['total_confirmed'][i],each['total_deaths'][i])
    # display(each)
    every_country_data=every_country_data.append(each)
# pd.set_option('display.max_rows', None)
# every_country_data

# Death Rate

## Countries with >50,00,000 cases (Projected starting 1000 case mark to calculate rise of deaths in terms of percentage).

In [ ]:
#hide_input
source= every_country_data[every_country_data.total_confirmed>atLeast]
# display(source)

scales = alt.selection_interval(bind='scales', zoom=True)
selection = alt.selection_multi(fields=['location'], bind='legend')
alt.data_transformers.disable_max_rows()

base = alt.Chart(source, title = "Death rate").encode(
    x = alt.X('date:T', title = "Days passed"),
    y = alt.Y("death_rate:Q",title = "Percentage"),
    color = alt.Color('location:N', legend=alt.Legend(title="Country",values=countries.to_list(), labelFontSize=15, titleFontSize=17),
                     scale=alt.Scale(scheme='tableau20')),
    opacity = alt.condition(selection, alt.value(1), alt.value(0.1))
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)
lines

alt.Chart(...)

In [ ]:
#hide-input
source=every_country_data[every_country_data.total_confirmed>atLeast]

death_table=pd.DataFrame(columns={'Country','Death rate'})
for each in countries:
    temp=source[source['location']==each]
    # display(temp)
    death_table=death_table.append([{'Country':each, 'Death rate' : temp.death_rate.tail(1).to_list()[0]}])
death_table=death_table.reset_index().drop('index',axis=1)
death_table

Country  Death rate
0          Belgium   15.589111
1   United Kingdom   15.380072
2            Italy   14.376356
3           France   14.325510
4      Netherlands   11.981621
5           Mexico   11.662482
6            Spain   11.070498
7           Canada    8.015406
8          Ecuador    7.373868
9           Sweden    7.295957
10           China    5.446695
11            Iran    5.039039
12           Egypt    4.775408
13       Indonesia    4.721784
14         Germany    4.528675
15            Iraq    4.091393
16   United States    3.976776
17          Brazil    3.847419
18        Colombia    3.751045
19         Bolivia    3.731299

# Infection-spread rates

## Countries with >50,00,000 cases (Projected starting 1000 case mark to calculate rise of infection in terms of percentage)

In [ ]:
#hide_input
source= every_country_data[every_country_data.total_confirmed>atLeast]

scales = alt.selection_interval(bind='scales', zoom=True)
selection = alt.selection_multi(fields=['location'], bind='legend')
alt.data_transformers.disable_max_rows()

base = alt.Chart(source, title = "Infection-spread rate").encode(
    x = alt.X('date:T', title = "Days passed"),
    y = alt.Y("percent_change:Q",title = "Percentage"),
    color = alt.Color('location:N', legend=alt.Legend(title="Country",values=countries.to_list(), labelFontSize=15, titleFontSize=17),
                     scale=alt.Scale(scheme='tableau20')),
    opacity = alt.condition(selection, alt.value(1), alt.value(0.1))
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)
lines


alt.Chart(...)

In [ ]:
#hide_input
source= every_country_data[every_country_data.total_confirmed>atLeast]

death_table=pd.DataFrame(columns={'Country','Spread rate'})
for each in countries:
    temp=source[source['location']==each]
    # display(temp)
    death_table=death_table.append([{'Country':each, 'Spread rate' : temp.percent_change.tail(1).to_list()[0]}])
death_table=death_table.reset_index().drop('index',axis=1)
death_table

Country  Spread rate
0          Belgium     0.118009
1   United Kingdom     0.425107
2            Italy     0.046869
3           France     0.000000
4      Netherlands     0.105247
5           Mexico     2.316094
6            Spain     0.260204
7           Canada     0.332776
8          Ecuador     1.622869
9           Sweden     0.230792
10           China     0.128059
11            Iran     0.970915
12           Egypt     1.119264
13       Indonesia     2.066744
14         Germany     0.137876
15            Iraq     2.535900
16   United States     2.003979
17          Brazil     2.220569
18        Colombia     2.547110
19         Bolivia     3.283249

# Cases Per Million Population

In [ ]:
#hide
cdata = data.rename(columns={"total_confirmed": "total_cases"})
# ddata.columns

# Population data
data_pop=pd.read_csv("data_files/world_population.csv")[["country","population"]]
data_pop=data_pop[data_pop.country.isin(cases_countries)]
# To list the countries who's population is not found in world bank
# pd.set_option('display.max_rows', None)
# countries=countries[~countries.isin(data_pop.country)]
cases_countries=cases_countries[cases_countries.isin(data_pop.country)]


# display(data_pop.country.unique().size , countries.size)
# (countries.isin(data_pop.country))[countries == False]
data_pc=cdata.copy()
data_pc=data_pc[data_pc.location.isin(cases_countries)]
# data_pc

In [ ]:
#hide
for i in cases_countries:
    data_pc.loc[data_pc.location == i,"total_cases"] = data_pc.loc[data_pc.location == i,"total_cases"]/(data_pop.loc[data_pop.country == i, "population"].astype(float).to_list()[0]/1000000)
# display(cases_countries)
data_countries_pc=[]

ranked_data=pd.DataFrame(columns=['country','total_cases_per_milliion_pop'])#country, total_cases_per_milliion_pop
# ranked_data.append({'a','b'})
# display(ranked_data)
for i in cases_countries:
    filter_country = data_pc["location"]== i
    temp=data_pc[filter_country]
    # display(temp)
    # if temp['total_cases'].tail(1).to_list()[0]> 500:
    if temp['total_cases'].sum() > 0 :
        ranked_data=ranked_data.append([{'country':i,'total_cases_per_milliion_pop':temp['total_cases'].tail(1).to_list()[0]}])

ranked_data=ranked_data.sort_values(by='total_cases_per_milliion_pop',ignore_index=True,ascending=False)
cases_countries=ranked_data['country']
# countries=countries[0:20]
for i in cases_countries:
    filter_country = data_pc["location"]== i
    # temp=data_pc[filter_country]
    data_countries_pc.append(data_pc[filter_country])
# pd.set_option('display.max_rows', None)
# display(ranked_data)
for i in range(0,len(cases_countries)):
    data_countries_pc[i]=data_countries_pc[i].reset_index()
    data_countries_pc[i]['x_day'] = data_countries_pc[i].index
len(data_countries_pc)

data_plot=pd.DataFrame()
for i in range(0,len(cases_countries)):
    data_plot = pd.concat([data_plot, data_countries_pc[i]], axis=0)
# data_plot

data_plot_death_log=data_plot.copy()
def a(x):
    if x==0:
        return 0
    return np.log(x)
pd.set_option('display.max_rows', 100)

# data_plot['total_log_cases']=data_plot['total_cases'].apply(a)
data_plotdata_plot=pd.DataFrame()
for i in range(0,len(cases_countries)):
    data_plot = pd.concat([data_plot, data_countries_pc[i]], axis=0)
# data_plot

data_plot_death_log=data_plot.copy()
def a(x):
    if x==0:
        return 0
    return np.log(x)
pd.set_option('display.max_rows', 100)

data_plot['total_log_cases']=data_plot['total_cases'].apply(a)
# cases_countries

In [ ]:
#hide_input
# Plot it using Altair
source = data_plot

scales = alt.selection_interval(bind='scales', zoom=True)
selection = alt.selection_multi(fields=['location'], bind='legend')
alt.data_transformers.disable_max_rows()

base = alt.Chart(source, title = "Highest COVID-19 Cases Per Million of Inhabitants").encode(
    x = alt.X('date:T', title = "Days passed"),
    y = alt.Y("total_cases:Q",title = "Cases per million"),
    color = alt.Color('location:N', legend=alt.Legend(title="Country",values=cases_countries.to_list(), labelFontSize=15, titleFontSize=17),
                     scale=alt.Scale(scheme='tableau20')),
    opacity = alt.condition(selection, alt.value(1), alt.value(0.1))
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)
lines

alt.Chart(...)

In [ ]:
#hide
# ddata = ddata.rename(columns={"total_deaths": "total_cases"})
# ddata.columns

# Population data
# data_pop=pd.read_csv("data_files/world_population.csv")[["country","population"]]
# data_pop=data_pop[data_pop.country.isin(countries)]
# To list the countries who's population is not found in world bank
# pd.set_option('display.max_rows', None)
# countries=countries[~countries.isin(data_pop.country)]
# countries=countries[countries.isin(data_pop.country)]


# display(data_pop.country.unique().size , countries.size)
# (countries.isin(data_pop.country))[countries == False]
# data_pc=ddata.copy()
# data_pc=data_pc[data_pc.location.isin(countries)]

In [ ]:
#hide_input

source=data_plot

death_table=pd.DataFrame(columns={'Country','Patients/ml','Total Population'})
for each in cases_countries:
    temp=source[source['location']==each]
    # display(temp)
    death_table=death_table.append([{'Country':each, 'Patients/ml' : temp.total_cases.tail(1).to_list()[0], 'Total Population':data_pop.loc[data_pop.country == each, "population"].astype(int).to_list()[0]}])
death_table=death_table.reset_index().drop('index',axis=1)
death_table

Patients/ml Total Population         Country
0   16713.205725         19116201           Chile
1   10367.210020        331002651   United States
2   10125.818221         32971854            Peru
3    9064.872435        212559417          Brazil
4    7525.399126         10099265          Sweden
5    5488.615516         46754778           Spain
6    5417.001053         11589623         Belgium
7    5062.457420        145934462          Russia
8    5029.482189         59308690    South Africa
9    4357.655143         11673021         Bolivia
10   4315.042167         67886011  United Kingdom
11   4024.754396         60461826           Italy
12   3943.194869         17643054         Ecuador
13   3211.716312         65273511          France
14   3121.369152         83992949            Iran
15   3032.001464         50882891        Colombia
16   2997.512908         17134872     Netherlands
17   2923.786491         37742154          Canada
18   2549.150799         84339067          Turkey
19   2415.879540        128932753          Mexico
20   2392.534837         83783942         Germany
21   2365.486649         45195774       Argentina
22   2032.618913         40222493            Iraq
23   1278.897525         43733762         Ukraine
24   1157.889857        220892340        Pakistan
25   1154.033105        164689383      Bangladesh
26    820.154286        102334404           Egypt
27    678.389873       1380004385           India
28    525.136283        109581078     Philippines
29    287.258561        273523615       Indonesia
30     59.212528       1439323776           China

# Deaths Per Million Population

In [ ]:
#hide
for i in countries:
    data_pc.loc[data_pc.location == i,"total_cases"] = data_pc.loc[data_pc.location == i,"total_cases"]/(data_pop.loc[data_pop.country == i, "population"].astype(float).to_list()[0]/1000000)

data_countries_pc=[]

ranked_data=pd.DataFrame(columns=['country','total_cases_per_milliion_pop'])#country, total_cases_per_milliion_pop
# ranked_data.append({'a','b'})
for i in countries:
    filter_country = data_pc["location"]== i
    temp=data_pc[filter_country]
    # display(temp)
    # if temp['total_cases'].tail(1).to_list()[0]> 500:
    if temp['total_cases'].sum() > 0 :
        ranked_data=ranked_data.append([{'country':i,'total_cases_per_milliion_pop':temp['total_cases'].tail(1).to_list()[0]}])

ranked_data=ranked_data.sort_values(by='total_cases_per_milliion_pop',ignore_index=True,ascending=False)
# display(ranked_data)
countries=ranked_data['country']
countries=countries[0:20]
for i in countries:
    filter_country = data_pc["location"]== i
    # temp=data_pc[filter_country]
    data_countries_pc.append(data_pc[filter_country])
# pd.set_option('display.max_rows', None)
# display(ranked_data)
for i in range(0,len(countries)):
    data_countries_pc[i]=data_countries_pc[i].reset_index()
    data_countries_pc[i]['x_day'] = data_countries_pc[i].index
len(data_countries_pc)

data_plot=pd.DataFrame()
for i in range(0,len(countries)):
    data_plot = pd.concat([data_plot, data_countries_pc[i]], axis=0)
# data_plot

data_plot_death_log=data_plot.copy()
def a(x):
    if x==0:
        return 0
    return np.log(x)
pd.set_option('display.max_rows', 100)

# data_plot['total_log_cases']=data_plot['total_cases'].apply(a)
data_plotdata_plot=pd.DataFrame()
for i in range(0,len(countries)):
    data_plot = pd.concat([data_plot, data_countries_pc[i]], axis=0)
# data_plot

data_plot_death_log=data_plot.copy()
def a(x):
    if x==0:
        return 0
    return np.log(x)
pd.set_option('display.max_rows', 100)

data_plot['total_log_cases']=data_plot['total_cases'].apply(a)

In [ ]:
#hide can be removed
# ddata = ddata.rename(columns={"total_deaths": "total_cases"})
# ddata.columns

# # Population data
# data_pop=pd.read_csv("data_files/world_population.csv")[["country","population"]]
# data_pop=data_pop[data_pop.country.isin(countries)]
# # To list the countries who's population is not found in world bank
# # pd.set_option('display.max_rows', None)
# # countries=countries[~countries.isin(data_pop.country)]
# countries=countries[countries.isin(data_pop.country)]


# # display(data_pop.country.unique().size , countries.size)
# # (countries.isin(data_pop.country))[countries == False]
# data_pc=ddata.copy()
# data_pc=data_pc[data_pc.location.isin(countries)]


In [ ]:
#hide_input
# Plot it using Altair
source = data_plot

scales = alt.selection_interval(bind='scales', zoom=True)
selection = alt.selection_multi(fields=['location'], bind='legend')
alt.data_transformers.disable_max_rows()

base = alt.Chart(source, title = "20 Highest COVID-19 Deaths Per Million of Inhabitants").encode(
    x = alt.X('date:T', title = "Days passed"),
    y = alt.Y("total_cases:Q",title = "Deaths per million"),
    color = alt.Color('location:N', legend=alt.Legend(title="Country",values=countries.to_list(), labelFontSize=15, titleFontSize=17),
                     scale=alt.Scale(scheme='tableau20')),
    opacity = alt.condition(selection, alt.value(1), alt.value(0.1))
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)

lines = base.mark_line().add_selection(
    scales
).add_selection(
    selection
).properties(
    width=chart_width,
    height=chart_height
)
lines

alt.Chart(...)

In [ ]:
#hide_input

source=data_plot

death_table=pd.DataFrame(columns={'Country','Deaths/ml','Total Population'})
for each in countries:
    temp=source[source['location']==each]
    # display(temp)
    death_table=death_table.append([{'Country':each, 'Deaths/ml' : temp.total_cases.tail(1).to_list()[0], 'Total Population':data_pop.loc[data_pop.country == each, "population"].astype(int).to_list()[0]}])
death_table=death_table.reset_index().drop('index',axis=1)
death_table

Total Population         Country   Deaths/ml
0          10099265          Sweden  745.143248
1          11589623         Belgium  467.400972
2          11673021         Bolivia  373.309972
3          17643054         Ecuador  223.498430
4          17134872     Netherlands  174.936405
5          46754778           Spain  117.391543
6          37742154          Canada   77.467399
7          60461826           Italy   66.566868
8          67886011  United Kingdom   63.563054
9          50882891        Colombia   59.587838
10         40222493            Iraq   50.534384
11         65273511          France   49.203977
12        212559417          Brazil   42.646299
13         83992949            Iran   37.162276
14        331002651   United States   31.320625
15         83783942         Germany   28.556007
16        128932753          Mexico   18.737516
17        102334404           Egypt    8.014453
18        273523615       Indonesia    1.050215
19       1439323776           China    0.041139

>The data suggests that with increasing number of cases increases death rate up to a certain point but also slows down the spread(rate) of the virus.

Updated daily by [GitHub Actions](https://github.com/features/actions).

This visualization was made by [Guneet Singh](https://github.com/guneetgstar).

- Data sourced from [World Bank](https://data.worldbank.org/indicator/SP.POP.TOTL) ["2019 Novel Coronavirus COVID-19 (2019-nCoV) Data Repository by Johns Hopkins CSSE"](https://systems.jhu.edu/research/public-health/ncov/), [GitHub repository](https://github.com/CSSEGISandData/COVID-19). Link to [original notebook](https://github.com/guneetgstar/covid19/blob/master/_notebooks/2020-05-15-relation-in-deaths-and-number-of-cases.ipynb).